# Run Finnish ASR models
Below you can see example code using Huggingface's `transformers` and `datasets` libraries to run our Finnish ASR models released at Huggingface model hub.

On Common Voice 7.0 Finnish test dataset, our best model is [Finnish-NLP/wav2vec2-xlsr-1b-finnish-lm-v2](https://huggingface.co/Finnish-NLP/wav2vec2-xlsr-1b-finnish-lm-v2) which is quite large model having 1B parameters. We also have smaller 300M and 95M parameter model versions: [Finnish-NLP/wav2vec2-large-uralic-voxpopuli-v2-finnish](https://huggingface.co/Finnish-NLP/wav2vec2-large-uralic-voxpopuli-v2-finnish), [Finnish-NLP/wav2vec2-xlsr-300m-finnish-lm](https://huggingface.co/Finnish-NLP/wav2vec2-xlsr-300m-finnish-lm) and [Finnish-NLP/wav2vec2-base-fi-voxpopuli-v2-finetuned](https://huggingface.co/Finnish-NLP/Finnish-NLP/wav2vec2-base-fi-voxpopuli-v2-finetuned). Note: the *Finnish-NLP/wav2vec2-large-uralic-voxpopuli-v2-finnish* model having 300M parameters is almost as good as the 1B parameter model so we advice you to use that. Also, the 95M parameter *Finnish-NLP/wav2vec2-base-fi-voxpopuli-v2-finetuned* is quite competitive model for its size. See model pages for more in-depth test comparisons.

Because those models are rather large, running the tests using GPU is highly recommended so you should enable the free GPU accelerator in Kaggle or Colab if you are running this notebook on those services. It's also possible to run the model testing with CPU but it will be a lot slower with large test datasets.

# 1. Install libraries

In [ ]:
!pip install -U transformers[torch-speech]==4.16.2 datasets[audio]==1.18.3 huggingface_hub==0.4.0 librosa==0.9.0 torchaudio==0.10.2 jiwer==2.3.0 requests==2.27.1 https://github.com/kpu/kenlm/archive/master.zip

In [ ]:
import os
import re
import requests
import torch
from transformers import AutoModelForCTC, AutoProcessor, AutoConfig, pipeline
from datasets import load_dataset, Audio, load_metric
from huggingface_hub import notebook_login

# 2. Create test dataset
We'll use Huggingface's `datasets` library to create test dataset which offers easy methods for resampling audio data etc.
Basically, you have two options to create the test dataset:
1. Use ready dataset available at Huggingface's dataset hub (like Mozilla's Common Voice 7.0)
2. Load your own custom dataset from local audio files

Below you can see examples of both methods for creating the test dataset.

## Option 1: Use ready dataset from Huggingface dataset hub
Let's load Mozilla's Common Voice 7.0 from hub: https://huggingface.co/datasets/mozilla-foundation/common_voice_7_0

Note: loading Common Voice 7.0 requires that you have a Huggingface user account (it's free) and that you have clicked "Access repository" on the dataset hub page: https://huggingface.co/datasets/mozilla-foundation/common_voice_7_0

After clicked "Access repository" you need to also do the Huggingface hub notebook login and paste your Huggingface access token available in your Huggingace account settings: https://huggingface.co/settings/token

This is not neccessary for the most datasets available at Huggingface hub but for Common Voice 7.0 it is

In [ ]:
# do huggingface hub notebook login to be able to access the Common Voice 7.0 dataset
notebook_login()

In [ ]:
# load Common Voice 7.0 dataset from Huggingface with Finnish "test" split
test_dataset = load_dataset("mozilla-foundation/common_voice_7_0", "fi", split="test", use_auth_token=True)

## Option 2: Load custom dataset from local audio files
We can also load our own custom dataset from local audio files with `datasets` library. Basically you need for example an Excel/CSV/Text file having two columns: one for the transcription texts and one for the audio filepaths. You can read more about loading local data from datasets' documentation: https://huggingface.co/docs/datasets/loading.html#local-and-remote-files

In [ ]:
# Let's download a small Finnish parliament session 2 dataset (147 audio samples) to demonstrate ASR dataset creation with custom audio files
# It's available here https://b2share.eudat.eu/records/4df422d631544ce682d6af1d4714b2d4

parliament_dataset_download_path = "./parliament_session_2"

os.mkdir(parliament_dataset_download_path)

parliament_files = ["%.2d" % i for i in range(1, 148)]

for file in parliament_files:
  url = f"https://b2share.eudat.eu/api/files/027d2358-f28d-4f73-8a51-c174989388f9/session_2_SEG_{file}.wav"
  response = requests.get(url)
  file_name = url.split('/')[-1]
  file = open(os.path.join(parliament_dataset_download_path, file_name), "wb")
  file.write(response.content)
  file.close()

url = "https://b2share.eudat.eu/api/files/027d2358-f28d-4f73-8a51-c174989388f9/session_2.trn.trn"
response = requests.get(url)
file = open(os.path.join(parliament_dataset_download_path, "transcript.csv"), "wb")
file.write(response.content)
file.close()

In [ ]:
# Let's load the local transcript CSV file so that it will have transcriptions in "sentence" column and audio file paths in "audio" column
test_dataset = load_dataset("csv", data_files=[os.path.join(parliament_dataset_download_path, "transcript.csv")], delimiter="(", column_names=["sentence", "audio"], split="train", encoding="latin-1")

In [ ]:
# We need to fix the audio filepaths so that they match with the local directory paths because they are a bit different than the original paths
def fix_parliament_audio_paths(batch):
    batch["audio"] = os.path.join(parliament_dataset_download_path, batch["audio"].split(")")[0]+".wav")
    batch["sentence"] = batch["sentence"].strip()
    return batch

test_dataset = test_dataset.map(fix_parliament_audio_paths)

## Process audio files into numerical arrays inside the dataset
Note: this is needed for the dataset loaded from own local files. For Common Voice 7.0 loaded from the Huggingface model hub, this has already been done automatically for you

In [ ]:
# Let's check one example of the test_dataset
# You should see "sentence" key having the transcription text and "audio" key having the path to the audio file
test_dataset[0]

In [ ]:
# Let's decode audio files into arrays inside the dataset
# Documentation about audio processing: https://huggingface.co/docs/datasets/audio_process.html
test_dataset = test_dataset.cast_column("audio", Audio())

In [ ]:
# Let's check one example of the test_dataset
# You should see "array" and "sampling_rate" keys inside the "audio" dict
test_dataset[0]

# 3. Load Finnish ASR model for testing
We'll use Huggingface's `transformers` library to easily load and use models available at Huggingface's model hub


In [ ]:
# Hugginface model hub's model ID
# e.g. "Finnish-NLP/wav2vec2-xlsr-1b-finnish-lm-v2" for the best 1B parameter model
# e.g. "Finnish-NLP/wav2vec2-large-uralic-voxpopuli-v2-finnish" for the smaller 300M parameter model (actually almost as good as the 1B model)
# e.g. "Finnish-NLP/wav2vec2-xlsr-300m-finnish-lm" for the smaller 300M parameter model
# e.g. "Finnish-NLP/wav2vec2-base-fi-voxpopuli-v2-finetuned" for the smaller 95M parameter model (actually better than the bigger Finnish-NLP/wav2vec2-xlsr-300m-finnish-lm model)
asr_model_name = "Finnish-NLP/wav2vec2-xlsr-1b-finnish-lm-v2"

In [ ]:
# load model's processor
processor = AutoProcessor.from_pretrained(asr_model_name)

In [ ]:
# OPTIONAL: change decoder's default alpha and beta parameters for language model decoding
# Check this video for learning more about those parameters: https://youtu.be/mp7fHMTnK9A?t=1418
# TLDR: alpha is the weight of the LM so lower the alpha for LM to have less effect and higher the alpha to increase its effect
processor.decoder.reset_params(
    alpha=0.5, # 0.5 by default
    beta=1.5, # 1.5 by default
)

In [ ]:
# load model and its config
model = AutoModelForCTC.from_pretrained(asr_model_name)
config = AutoConfig.from_pretrained(asr_model_name)

In [ ]:
# Let's use Huggingface's easy-to-use ASR pipeline loaded with our model to transcribe our audio data
# To use GPU in the ASR pipeline, "device" needs to be 0, for CPU it should be -1
device = 0 if torch.cuda.is_available() else -1
asr = pipeline("automatic-speech-recognition", model=model, config=config, tokenizer=processor.tokenizer, feature_extractor=processor.feature_extractor, decoder=processor.decoder, device=device)

# 4. Resample test dataset to the correct sampling rate required by the model
Our models are trained with audio data sampled at 16000 kHz so you need to use them with audio sampled at the same 16000 kHz. Luckily, Huggingface's `datasets` library offers easy ready method for resampling our testing dataset into correct sampling rate.

In [ ]:
# Get the model's sampling rate (16000 with our models)
sampling_rate = processor.feature_extractor.sampling_rate

# Resample our test dataset
test_dataset = test_dataset.cast_column("audio", Audio(sampling_rate=sampling_rate))

# 5. Run test dataset through the model's ASR pipeline to get predicted transcriptions

In [ ]:
# Test dataset's true target transcriptions can e.g. include special characters not relevant for ASR testing,
# so let's create target transcription text normalization function
def normalize_text(text: str) -> str:
    """DO ADAPT FOR YOUR USE CASE. this function normalizes the target text transcription."""

    CHARS_TO_IGNORE = [",", "?", "¿", ".", "!", "¡", ";", "；", ":", '""', "%", '"', "�", "ʿ", "·", "჻", "~", "՞",
                   "؟", "،", "।", "॥", "«", "»", "„", "“", "”", "「", "」", "‘", "’", "《", "》", "(", ")", "[", "]",
                   "{", "}", "=", "`", "_", "+", "<", ">", "…", "–", "°", "´", "ʾ", "‹", "›", "©", "®", "—", "→", "。",
                   "、", "﹂", "﹁", "‧", "～", "﹏", "，", "｛", "｝", "（", "）", "［", "］", "【", "】", "‥", "〽",
                   "『", "』", "〝", "〟", "⟨", "⟩", "〜", "：", "！", "？", "♪", "؛", "/", "\\", "º", "−", "^", "ʻ", "ˆ"]
    
    chars_to_remove_regex = f"[{re.escape(''.join(CHARS_TO_IGNORE))}]"

    text = re.sub(chars_to_remove_regex, "", text.lower())
    text = re.sub("[-]", " ", text)

    # In addition, we can normalize the target text, e.g. removing new lines characters etc...
    # note that order is important here!
    token_sequences_to_ignore = ["\n\n", "\n", "   ", "  "]

    for t in token_sequences_to_ignore:
        text = " ".join(text.split(t))

    return text

In [ ]:
# function used to get predicted transcriptions by the model and also do the target transcription normalization at the same time
def map_to_pred(batch):
    prediction = asr(batch["audio"]["array"])
    # for very long audios (e.g. over 30 min) you may have to add audio chunking to avoid memory errors, read more here: https://huggingface.co/blog/asr-chunking
    # for example: prediction = asr(batch["audio"]["array"], chunk_length_s=6, stride_length_s=(2, 2))

    batch["prediction"] = prediction["text"]
    batch["target"] = normalize_text(batch["sentence"]) # normalize target text (e.g. make it lower case and remove punctuation)
    return batch

In [ ]:
# Let's run our test dataset with the previosly defined function to get the results
# This can take some time with large test datasets or if you run with CPU
result = test_dataset.map(map_to_pred, remove_columns=test_dataset.column_names)

In [ ]:
# Let's check one example of the results
# You should see "prediction" key having the model's transcription prediction and "target" key having the original target transcription
result[0]

# 6. Compute WER and CER metrics for the results
Let's use Huggingface's `datasets` library's standard WER (Word Error Rate) and CER (Character Error Rate) metric methods

In [ ]:
# load ASR metrics from Huggingface's datasets library
wer = load_metric("wer")
cer = load_metric("cer")

In [ ]:
# compute ASR metrics
wer_result = wer.compute(references=result["target"], predictions=result["prediction"])
cer_result = cer.compute(references=result["target"], predictions=result["prediction"])

In [ ]:
# print metric results
result_str = f"WER: {wer_result}\n" f"CER: {cer_result}"
print(result_str)